In [1]:
import pandas as pd
from pathlib import Path
import numpy as np
from scipy.stats import ranksums
import matplotlib.pyplot as plt
import chart_studio
import chart_studio.tools as tls
import chart_studio.plotly as py
import plotly.express as px
%matplotlib inline
import cufflinks as cf
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
cf.go_offline()
import dash_bio as dashbio
import os

In [4]:
%ls tmp_output

20-07-m2_ci_no_skew               20-07-m2_ssa_ci_no_skew
20-07-m2_ci_skew                  20-07-m2_ssa_ci_skew
20-07-m2_fits_no_skew             20-07-m2_wt_fits_no_skew
20-07-m2_fits_skew                20-07-m2_wt_fits_skew
20-07-m2_results_ci_no_skew       20-07-method1_skewed_removed.csv
20-07-m2_results_ci_skew          20-07-method1_with_skewed.csv
20-07-m2_results_fit_no_skew      method1_skewed_removed.csv
20-07-m2_results_fit_skew         skewed_samples.txt


In [113]:
ssa=pd.read_csv(resultsDir/"20-07-m2_ssa_ci_no_skew")

In [118]:
new = ssa['Unnamed: 0'].str.split("_", expand=True)
new.columns = ['mouse', 'day', 'dnaid', 'experiment']
ssa = pd.concat([ssa, new], axis=1)

In [120]:
ssa.groupby(['library', 'day']).ssa_ci.median()

library       day
library_10_1  d0      1.001209
              d1      2.247114
              d2      2.733694
              d3      3.438981
              d4      2.447038
library_10_2  d0      0.880295
              d1      1.357132
              d2      1.343162
              d3      1.375334
              d4      1.964898
library_11_1  d0      0.922646
              d1      1.356210
              d2      0.921910
              d3      1.805304
library_11_2  d0      1.000000
              d1      1.440038
              d2      1.213544
              d3      0.905257
library_12_1  d0      1.000005
              d1      0.975234
              d2      1.164609
              d3      2.625035
              d4      2.946970
library_12_2  d0      1.081502
              d1      1.164846
              d2      1.829743
              d3      1.592452
library_13_1  d0      1.001754
              d1      1.624833
              d2      3.892634
              d3      1.588585
              d4     

In [108]:
resultsDir = Path("tmp_output")

res_m1 = pd.read_csv(resultsDir/"20-07-method1_skewed_removed.csv", index_col=0)
res_m1.columns = ["m1_"+c if c not in ['library', 'ShortName', 'day'] else c for c in res_m1.columns ]
res_m2 = pd.read_csv(resultsDir/"20-07-m2_results_ci_no_skew", index_col=0)
res_m2.columns = ["m2_"+c if c not in ['library', 'ShortName', 'day'] else c for c in res_m2.columns ]

#
res_m1s = pd.read_csv(resultsDir/"20-07-method1_with_skewed.csv", index_col=0)
res_m1s.columns = ["m1_"+c if c not in ['library', 'ShortName', 'day'] else c for c in res_m1s.columns ]
res_m2s = pd.read_csv(resultsDir/"20-07-m2_results_ci_skew", index_col=0)
res_m2s.columns = ["m2_"+c if c not in ['library', 'ShortName', 'day'] else c for c in res_m2s.columns ]

In [18]:
res_m1.sample(5)

m1_gene day  m1_gene_FC  m1_gene_FC_median  m1_sigma  m1_zscore  \
847   SL1344_RS24575  d2    0.085187           0.193036  0.210529   0.697769   
1356            dsdA  d1    0.049936           0.049936  0.343516  -0.038959   
1363            oppA  d2   -0.241191          -0.241191  0.246520  -1.734823   
1722            rfbH  d1   -3.380672          -3.380672  0.829043  -3.649377   
1987            yeeN  d2   -0.234588          -0.234588  0.294042  -1.504725   

         m1_ci   m1_pval   m1_padj  m1_n_samples       library  \
847   1.121672  0.485322  0.882253           4.0   library_9_1   
1356  0.989371  0.968923  0.999701           6.0  library_13_1   
1363  0.701341  0.082772  0.470828           3.0  library_11_2   
1722  0.120831  0.000263  0.003240           6.0   library_9_1   
1987  0.704558  0.132395  0.560628           3.0  library_11_2   

           ShortName  m1_num_barcodes  \
847   SL1344_RS24575              4.0   
1356            dsdA              1.0   
1363            oppA              2.0   
1722            rfbH              1.0   
1987            yeeN              1.0   

                                             m1_barcode m1_control  
847   AGTCTACCCGTTAACAC, ACGTAGGGCAAGACGCA, GACCGCTA...        NaN  
1356                                  CGGACCACGAGCGCACA        NaN  
1363               CGCGTGCCCAGTCGGAA, GATACTTTACCAAGACG        NaN  
1722                                  ATATACAACACGAACAC        NaN  
1987                                  CCCATCACCCACCTAAG        NaN

In [19]:
res_m2.sample(5)

ShortName day     m2_ci   m2_pval   m2_padj       library
2346                kbl  d1  0.886386  0.772830  0.831600  library_12_2
2976  TGGTTCAAAAGCGCATA  d1  2.371003  0.897987  0.908938  library_10_1
2772               dpaL  d1  0.395870  0.003948  0.035273  library_13_1
1520        SL1344_2341  d1  1.107256  0.105969  0.164856  library_10_2
1412     SL1344_RS24615  d3  0.564699  0.121335  0.183140  library_11_2

In [62]:
resultsNoSkew = res_m1.merge(res_m2, on=['library', 'day', 'ShortName'])
resultsNoSkew['m1_hits'] = (resultsNoSkew.m1_padj < 0.05).astype(int)
resultsNoSkew['m2_hits'] = (resultsNoSkew.m2_padj < 0.05).astype(int)*2
resultsNoSkew['hits_int'] = resultsNoSkew['m1_hits'] + resultsNoSkew['m2_hits']
hit_labels = {0: 'Not a hit', 1: 'Method 1 Hit', 2: 'Method 2 Hit', 3: 'Method 1 and 2 Hit'}
resultsNoSkew['hits'] = resultsNoSkew['hits_int'].map(hit_labels)

In [109]:
res_m1s.head()

m1_gene day  m1_gene_FC  m1_gene_FC_median  m1_sigma  m1_zscore  \
0  SL1344_0014  d1    0.138678           0.138678  0.091293   3.422489   
1  SL1344_0014  d2    0.089514           0.089514  0.091316   3.752748   
2  SL1344_0014  d3   -0.034684          -0.034684  0.091682  -0.434422   
3  SL1344_0015  d1    0.263348           0.263348  0.116180   3.820524   
4  SL1344_0015  d2    0.219084           0.219084  0.116202   4.152668   

      m1_ci   m1_pval   m1_padj  m1_n_samples       library    ShortName  \
0  1.539817  0.000621  0.006126           6.0  library_11_1  SL1344_0014   
1  1.605578  0.000175  0.001048           6.0  library_11_1  SL1344_0014   
2  0.946570  0.663982  0.878620           6.0  library_11_1  SL1344_0014   
3  1.678799  0.000133  0.002353           6.0  library_11_1  SL1344_0015   
4  1.756451  0.000033  0.000304           6.0  library_11_1  SL1344_0015   

   m1_num_barcodes                            m1_barcode m1_control  
0              2.0  CCTGTCGCGATAGCTTG, CGTGACAAGCCACTCGG        NaN  
1              2.0  CCTGTCGCGATAGCTTG, CGTGACAAGCCACTCGG        NaN  
2              2.0  CCTGTCGCGATAGCTTG, CGTGACAAGCCACTCGG        NaN  
3              1.0                     ATGAAAAGTATGAATCC        NaN  
4              1.0                     ATGAAAAGTATGAATCC        NaN

In [110]:
resultsSkew = res_m1s.merge(res_m2s, on=['library', 'day', 'ShortName'])
resultsSkew['m1_hits'] = (resultsSkew.m1_padj < 0.05).astype(int)
resultsSkew['m2_hits'] = (resultsSkew.m2_padj < 0.05).astype(int)*2
resultsSkew['hits_int'] = resultsSkew['m1_hits'] + resultsSkew['m2_hits']
hit_labels = {0: 'Not a hit', 1: 'Method 1 Hit', 2: 'Method 2 Hit', 3: 'Method 1 and 2 Hit'}
resultsSkew['hits'] = resultsSkew['hits_int'].map(hit_labels)

In [104]:
resultsNoSkew.groupby(['library', 'day']).agg({'m1_hits':['sum'], 'm2_hits':[lambda x: sum(x)/2]})

m1_hits  m2_hits
                     sum <lambda>
library      day                 
library_10_1 d1      114      773
             d2       63      846
             d3       71      828
             d4      308      707
library_10_2 d1       17      505
             d2       38      880
             d3       96        0
             d4       54      104
library_11_1 d1      348        0
             d2      629        0
             d3       80        0
library_11_2 d1       14        0
             d2       41        0
             d3      216        0
library_12_1 d1       23      161
             d2      176     1091
             d3      256     1022
             d4      520        0
library_12_2 d1       10        0
             d2       39        0
             d3       90        0
library_13_1 d1       13      114
             d2       22      556
             d3       28        0
             d4      685        0
library_13_2 d1       12        0
             d2       19        0
             d3       38        0
library_14_2 d1       32      850
             d2       64      921
             d3       63      694
             d4      242      732
library_15_1 d1       15        0
             d2       18        0
             d3      490        0
library_9_1  d1      276      469
             d2       50        0
             d3      131        0

In [47]:
px.scatter(resultsNoSkew[resultsNoSkew.day == 'd1'], x='m1_ci', y='m2_ci', color='library', log_x=True, log_y=True, hover_name='ShortName',
          hover_data=['day', 'library'])

In [50]:
px.scatter(resultsNoSkew[(resultsNoSkew.hits != 'Not a hit')& (resultsNoSkew.day == 'd1')], 
          x='m1_ci', y='m2_ci', color='library', log_x=True, log_y=True, hover_name='ShortName',
          hover_data=['day', 'library', 'hits'])

In [78]:
resultsNoSkew[(resultsNoSkew.library == 'library_10_2')&(resultsNoSkew.hits_int == 1)& (resultsNoSkew.day == 'd1')].shape

(0, 22)

In [57]:
px.scatter(resultsNoSkew[resultsNoSkew.day == 'd1'], x='m2_ci', y='m1_zscore', color='library', log_x=True, hover_name='ShortName',
          hover_data=['day', 'library', 'hits'])

In [102]:
gene = "purD"

px.box(resultsNoSkew[resultsNoSkew.ShortName == gene], x='day', y='m1_ci', points='all', color='m1_hits',
       hover_data=['library'])

In [103]:
px.box(resultsNoSkew[resultsNoSkew.ShortName == gene], x='day', y='m2_ci', points='all', color='m2_hits', 
       hover_data=['library'])

correlation matrices at mouse level

In [88]:
px.scatter(resultsNoSkew[(resultsNoSkew.ShortName == gene) &(resultsNoSkew.day == 'd1')], 
           x='m2_ci', y='m1_ci', hover_data=['library'], log_x=True, log_y=True)